In [1]:
from sklearn.preprocessing import LabelEncoder
from bio import AlignIO
from Bio.Align import MultipleSeqAlignment
from Bio.SeqRecord import SeqRecord
from Bio import SeqIO
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from keras_preprocessing import sequence
import sklearn
import numpy as np
import re

In [2]:
seq_length =10
def string_to_array(my_string):
    my_string = my_string.lower()
    my_string = re.sub('[^acgt0]', 'z', my_string)
    my_array = np.array(list(my_string))
    return my_array

def readmaf(start, end, filename):
    count = 0
    oldlist =[]
    align = AlignIO.parse(filename, "maf")
    for multiple_alignment in align:
        count = count+1
        if count >start and count<=end:
            oldlist.append(multiple_alignment)
        elif count>end:
            break
    return oldlist

#oldlist stores MSAs
oldlist = readmaf(0, 1000, "data/chr2.anc.maf")
print(oldlist[1][1])
print(dir(oldlist[1]))
print(oldlist[1][0].id)
#print(oldlist[2])

ID: panTro4.chr2A
Name: panTro4.chr2A
Number of features: 0
/start=4703
/size=1
/strand=1
/srcSize=113622374
Seq('a', SingleLetterAlphabet())
['__add__', '__class__', '__delattr__', '__dict__', '__dir__', '__doc__', '__eq__', '__format__', '__ge__', '__getattribute__', '__getitem__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__iter__', '__le__', '__len__', '__lt__', '__module__', '__ne__', '__new__', '__reduce__', '__reduce_ex__', '__repr__', '__setattr__', '__sizeof__', '__str__', '__subclasshook__', '__weakref__', '_alphabet', '_annotations', '_append', '_get_per_column_annotations', '_per_col_annotations', '_records', '_set_per_column_annotations', '_str_line', 'add_sequence', 'annotations', 'append', 'column_annotations', 'extend', 'format', 'get_alignment_length', 'sort']
hg38.chr2


In [3]:
print(len(oldlist))

1000


In [4]:
#alignList stores alignments between direct ancestor and descendent
def getAlign(inputList, keyword):
    alignList = []
    zeros = ''
    for i in range(len(inputList)):
        # index for the dog
        indexDes = -1
        indexAnc = -1

        for j in range(len(inputList[i])):
            if len(inputList[i][j])>=10 and 'canFam3' in inputList[i][j].id  :
                indexDes = j
            elif len(inputList[i][j])>=10 and inputList[i][j].id == '_CMAOL': #'_RMPC' :
                indexAnc = j
            '''    
            if j%1000000000 == 0 : 
                print(indexDes, indexAnc)'''
        if indexDes!=-1 and indexAnc!=-1:
            alignment = MultipleSeqAlignment([
                    SeqRecord(inputList[i][indexDes].seq+zeros, id=inputList[i][indexDes].id),
                    SeqRecord(inputList[i][indexAnc].seq+zeros, id=inputList[i][indexAnc].id),
                    #SeqRecord(zeros+inputList[i][indexDes].seq, id=inputList[i][indexDes].id)
                ]
            )
            alignList.append(alignment)
            '''
            if len(inputList[i][j])>=10 and j<len(inputList[i])-1 and (keyword[k] in inputList[i][j].id and keyword[k] in inputList[i][j+1].id):
                alignment = MultipleSeqAlignment([
                        SeqRecord(inputList[i][j].seq, id=inputList[i][j].id),
                        SeqRecord(inputList[i][j+1].seq, id=inputList[i][j+1].id)
                    ]
                )
                alignList.append(alignment)'''
    return alignList

def zeros(length):
    return "0"*length
    
FinalList = []    
anc = []
des = []
keyword = ["_HP","_RM","_FC","_CS","_BO","_PB","_TO","_VC", "_PP"]
alignList = getAlign(oldlist, keyword)
print(len(alignList))
print(alignList[126])
print(len(alignList[126][1].seq))
print(len(alignList[126][1]))
for i in range (100):
    print('printing new alignment -------------------------------------------\n')
    print(alignList[i])

#print(str(alignList[62][1]))
#print('The scikit-learn version is {}.'.format(sklearn.__version__))

369
SingleLetterAlphabet() alignment with 2 rows and 20 columns
GATG---------------- canFam3.chr17
GATG---------------- _CMAOL
20
20
printing new alignment -------------------------------------------

SingleLetterAlphabet() alignment with 2 rows and 34 columns
AAGAGAG-AAACTAAAGCTGAGCCATAGGCTACA canFam3.chr17
AAGACAG-AAACTAAAGCTGAGCCATAGGCTACA _CMAOL
printing new alignment -------------------------------------------

SingleLetterAlphabet() alignment with 2 rows and 238 columns
A----------CTGACCTGAC----AGTCAGAGGAA-AGCAGGG...--- canFam3.chr17
A----------CTGATCTGACAATAAGTCAGGGGAA-AGAAGGG...--- _CMAOL
printing new alignment -------------------------------------------

SingleLetterAlphabet() alignment with 2 rows and 79 columns
------------------------------------------AG...TTT canFam3.chr17
------------------------------------------AG...TTT _CMAOL
printing new alignment -------------------------------------------

SingleLetterAlphabet() alignment with 2 rows and 14 columns
GCATTGTGTG---T ca

In [5]:
label_encoder = LabelEncoder()
label_encoder.fit(np.array(['a','c','g','t','0', 'z']))
encoder = OneHotEncoder(sparse=False, dtype=int, categories=[range(6)])
def one_hot_encoder(my_array, encoder):
    integer_encoded = label_encoder.transform(my_array)
    integer_encoded = integer_encoded.reshape(len(integer_encoded), 1)
    onehot_encoded = encoder.fit_transform(integer_encoded)
    #onehot_encoded = np.delete(onehot_encoded, -1, 1)
    return onehot_encoded, encoder

def alignBoth(alignList):
    zeros = '00000'
    h, w = len(alignList), 2;
    Matrix = [[0 for x in range(w)] for y in range(h)]
    for i in range(len(alignList)):
        for j in range(len(alignList[i])):
            Matrix[i][j] = one_hot_encoder(string_to_array(str(alignList[i][j].seq).upper()), encoder)
    return Matrix

# [Index of alignment][1 for Ancester, 0 for Descendant][Always 0]
one_hot_aligned = alignBoth(alignList)
#one_hot_aligned = one_hot_aligned[:][:][0]
one_hot_aligned = np.array(one_hot_aligned)
#print(one_hot_aligned.shape)
#ignorethis, encoder = one_hot_encoder(string_to_array(str(alignList[1][1].seq)),encoder)


print(type(one_hot_aligned))
print(len(one_hot_aligned[126][1]))
print(one_hot_aligned[126][1][0])
#print(encoder.inverse_transform(one_hot_aligned[126][1]))
print(type(one_hot_aligned[126][1]))
# A = [1 0 0 0], C = [0 1 0 0], G = [0 0 1 0], T = [0 0 0 1]
def decoder(array):
    result = ""
    size = len(array)
    for i in range(size):
        if array[i].tolist() == [1, 0, 0, 0, 0, 0]:
            result=result+"0" 
        elif array[i].tolist() == [0, 1, 0, 0, 0, 0]:
            result=result+"A"
        elif array[i].tolist() == [0, 0, 1, 0, 0, 0]:
            result=result+"C"
        elif array[i].tolist() == [0, 0, 0, 1, 0, 0]:
            result=result+"G"
        elif array[i].tolist() == [0, 0, 0, 0, 1, 0]:
            result=result+"T"
        elif array[i].tolist() == [0, 0, 0, 0, 0, 1]:
            result=result+"-"
    return result

def decoderY(array):
    result = ""    
    if array.tolist() == [1, 0, 0, 0, 0, 0]:
        result=result+"0" 
    elif array.tolist() == [0, 1, 0, 0, 0, 0]:
        result=result+"A"
    elif array.tolist() == [0, 0, 1, 0, 0, 0]:
        result=result+"C"
    elif array.tolist() == [0, 0, 0, 1, 0, 0]:
        result=result+"G"
    elif array.tolist() == [0, 0, 0, 0, 1, 0]:
        result=result+"T"
    elif array.tolist() == [0, 0, 0, 0, 0, 1]:
        result=result+"-"
    return result
    
print(decoder(one_hot_aligned[126][1][0]))
print(len(one_hot_aligned))

<class 'numpy.ndarray'>
2
[[0 0 0 1 0 0]
 [0 1 0 0 0 0]
 [0 0 0 0 1 0]
 [0 0 0 1 0 0]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]
 [0 0 0 0 0 1]]
<class 'numpy.ndarray'>
GATG----------------
369


In [23]:
def vectorize(char_setx, char_sety, sequence_length):
    dataX = []
    dataY = []
    dataX1 = []
    dataY1 = []
    result=[]
    #print(type(char_sety[0]))
    for i in range(len(char_setx) - sequence_length):
        
        '''for i in char_sety[i: i + sequence_length-1]:
            y1.append(i)'''
        #x1 = char_setx1[i: i + sequence_length]
        x = char_setx[i:i + sequence_length]
        y = char_sety[i: i + sequence_length]
        y1 = [[1, 0, 0, 0, 0, 0]]
        temp = y[:-1]
        temp = temp.tolist()
        for i in temp:
            y1.append(i)
        y1=np.array(y1)
        if mutation_with_nogap(x, y):# and mutation_with_nogap(x1, y1)
            dataX.append(x)
            dataY.append(y)
            dataY1.append(y1)

    return dataX, dataY, dataY1

def tokenize(one_hot_aligned, sequence_length):
    X = []
    Y = []
    X1 = []
    Y1 = []
    for i in range(len(one_hot_aligned)):
        dataX, dataY, dataY1 = vectorize(one_hot_aligned[i][1][0], one_hot_aligned[i][0][0],  sequence_length)
        X.extend(dataX)
        Y.extend(dataY)
        #X1.extend(dataX1)
        Y1.extend(dataY1)
    return X, Y, Y1

def truncate(one_hot_aligned):
    X = []
    Y = []
    for i in range(len(one_hot_aligned)):
        X.append(one_hot_aligned[i][1][0])
        Y.append(one_hot_aligned[i][0][0])
    X = sequence.pad_sequences(X,
                                 maxlen=30,
                                 truncating='post',
                                 padding='post',
                                 value=0)
    Y = sequence.pad_sequences(Y,
                                 maxlen=30,
                                 truncating='post',
                                 padding='post',
                                 value=0)
    return X,Y

# function for checking if there are at least one mutation and there are no gaps.
def mutation_with_nogap(a, b):
    a = a.tolist()
    b = b.tolist()
    if a.count([0,0,0,0,0,1])>0 or b.count([0,0,0,0,0,1])>0:
        return False
    else:
        return True
def diffList(a, b):
    count = 0
    length = len(a)
    for i in range(length):
        if a[i] != b[i]:
            count = count+1
    return count

def deleteGap(one_hot_aligned):
    result = one_hot_aligned
    for i in range(len(one_hot_aligned)):
        if one_hot_aligned[i][1][0] == '-' and one_hot_aligned[i][0][0] == '-':
            result.pop(i)
    return result

# Used for non 0 padding
one_hot_aligned = deleteGap(one_hot_aligned)
X, Y, Y1=tokenize(one_hot_aligned, seq_length)
print(X[0].shape)
print(X[0][0].shape)
print(len(X))
print(X)
# Used for 0 padding
#X, Y = truncate(one_hot_aligned)
X = np.array(X)
Y = np.array(Y)
#X1 = np.array(X1)
Y1 = np.array(Y1)
print(X.shape)

/home/mcb/dlim63/miniconda3/envs/research/lib/python3.6/site-packages/ipykernel_launcher.py:78: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison


(10, 6)
(6,)
4320
[array([[0, 1, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 0, 1, 0, 0, 0],
       [0, 0, 0, 0, 1, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 0, 0, 1, 0, 0],
       [0, 0, 1, 0, 0, 0]]), array([[0, 1, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 0, 1, 0, 0, 0],
       [0, 0, 0, 0, 1, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 0, 0, 1, 0, 0],
       [0, 0, 1, 0, 0, 0],
       [0, 0, 0, 0, 1, 0]]), array([[0, 1, 0, 0, 0, 0],
       [0, 0, 1, 0, 0, 0],
       [0, 0, 0, 0, 1, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 0, 0, 1, 0, 0],
       [0, 0, 1, 0, 0, 0],
       [0, 0, 0, 0, 1, 0],
       [0, 0, 0, 1, 0, 0]]), array([[0, 0, 1, 0, 0, 0],
       [0, 0, 0, 0, 1, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 1, 0, 0, 0, 0],
       [0, 0, 0, 1, 0, 0],
   

In [8]:
print(Y.shape)
print(len(X))
pt1 = 9000000
pt2 = 9100000
pt3 = 9200000
X_train = X[:pt1]
X_val = X[pt1:pt2]
X_test = X[pt2:pt3]
y_train = Y[:pt1]
y_val =  Y[pt1:pt2]
y_test = Y[pt2:pt3]
# X_train1 = X1[:pt1]
# X_val1 = X1[pt1:pt2]
# X_test1 = X1[pt2:pt3]
y_train1 = Y1[:pt1]
y_val1 =  Y1[pt1:pt2]
y_test1 = Y1[pt2:pt3]

# X_train = X[:20000]
# X_val = X[20000:23000]
# X_test = X[23000:26000]
# y_train = Y[:20000]
# y_val =  Y[20000:23000]
# y_test = Y[23000:26000]

np.save('prepData/X_train_camFam3_v3_chr2_size3', X_train)
np.save('prepData/X_val_camFam3_v3_chr2_size3', X_val)
np.save('prepData/X_test_camFam3_v3_chr2_size3', X_test)
np.save('prepData/y_train_camFam3_v3_chr2_size3', y_train)
np.save('prepData/y_val_camFam3_v3_chr2_size3', y_val)
np.save('prepData/y_test_camFam3_v3_chr2_size3', y_test)

np.save('prepData/y_train1_camFam3_v3_chr2_size3', y_train1)
np.save('prepData/y_val1_camFam3_v3_chr2_size3', y_val1)
np.save('prepData/y_test1_camFam3_v3_chr2_size3', y_test1)

# np.save('prepData/X_train1_camFam3_1mutOnly_v2', X_train1)
# np.save('prepData/X_val1_camFam3_1mutOnly_v2', X_val1)
# np.save('prepData/X_test1_camFam3_1mutOnly_v2', X_test1)


# np.save('prepData20/X_train_camFam3_1mutOnly', X_train)
# np.save('prepData20/X_val_camFam3_1mutOnly', X_val)
# np.save('prepData20/X_test_camFam3_1mutOnly', X_test)
# np.save('prepData20/y_train_camFam3_1mutOnly', y_train)
# np.save('prepData20/y_val_camFam3_1mutOnly', y_val)
# np.save('prepData20/y_test_camFam3_1mutOnly', y_test)

print(X_train.shape)
print(X_val.shape)
print(X_test.shape)
print(X_train[0])
print(y_train[0])
print(y_train1[0])

/home/mcb/dlim63/miniconda3/envs/research/lib/python3.6/site-packages/ipykernel_launcher.py:78: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison


(9200586, 3, 6)
9200586
(9000000, 3, 6)
(100000, 3, 6)
(100000, 3, 6)
[[0 1 0 0 0 0]
 [0 1 0 0 0 0]
 [0 0 0 1 0 0]]
[[0 1 0 0 0 0]
 [0 1 0 0 0 0]
 [0 0 0 1 0 0]]
[[1 0 0 0 0 0]
 [0 1 0 0 0 0]
 [0 1 0 0 0 0]]


In [7]:
# import difflib
# sm=difflib.SequenceMatcher(None,X_test,X_train)
# sm2=difflib.SequenceMatcher(None,y_test,y_train)
for i in range(len(X)):
    print(i, decoder(X[i]))

0 AAG
1 AGA
2 GAC
3 ACA
4 CAG
5 AAA
6 AAC
7 ACT
8 CTA
9 TAA
10 AAA
11 AAG
12 AGC
13 GCT
14 CTG
15 TGA
16 GAG
17 AGC
18 GCC
19 CCA
20 CAT
21 ATA
22 TAG
23 AGG
24 GGC
25 GCT
26 CTA
27 TAC
28 CTG
29 TGA
30 GAT
31 ATC
32 TCT
33 CTG
34 TGA
35 GAC
36 AGT
37 GTC
38 TCA
39 CAG
40 AGG
41 GGG
42 GGG
43 GGA
44 GAA
45 AGA
46 GAA
47 AAG
48 AGG
49 GGG
50 GGC
51 GCA
52 CAC
53 ACA
54 CAG
55 AGA
56 GAG
57 AGA
58 GAG
59 AGA
60 TTT
61 TTG
62 TGA
63 GAA
64 AAC
65 ACA
66 CAT
67 ATT
68 TTT
69 TTG
70 TGT
71 GTC
72 TCC
73 CCA
74 CAC
75 ACT
76 CTA
77 TAA
78 AAA
79 AAA
80 AAT
81 ATG
82 TGC
83 GCT
84 CTA
85 TAG
86 AGA
87 GAA
88 AAT
89 ATT
90 TTC
91 TCA
92 CAT
93 ATA
94 AAA
95 AAT
96 ATT
97 TTG
98 TGA
99 GAT
100 ATT
101 TTC
102 TCC
103 CCA
104 CAA
105 AAG
106 AGT
107 AAA
108 TAA
109 AAT
110 ATA
111 TAA
112 AAT
113 ATA
114 TAA
115 AAT
116 ATC
117 TCA
118 CAA
119 AAT
120 ATA
121 TAA
122 CAA
123 AAA
124 GGA
125 GAT
126 ATC
127 TCT
128 CTA
129 TAC
130 ACA
131 CAG
132 AGT
133 GTA
134 TAG
135 AGG
136 GGA
137 GAA
138 AA

1364 TTT
1365 TTT
1366 TTC
1367 TCA
1368 CAT
1369 TTA
1370 TAG
1371 AGT
1372 GTG
1373 TGA
1374 GAT
1375 ATT
1376 TTT
1377 TTT
1378 TTA
1379 TAA
1380 AAG
1381 AGG
1382 GGT
1383 GTA
1384 TAA
1385 AAT
1386 ATG
1387 TGA
1388 GAA
1389 AAA
1390 AAT
1391 ATT
1392 TTG
1393 TGA
1394 GAG
1395 AGA
1396 GAA
1397 AAG
1398 AGT
1399 GTC
1400 TCT
1401 CTG
1402 TGT
1403 GTG
1404 TGT
1405 GTC
1406 TCT
1407 CTC
1408 TCT
1409 CTA
1410 TAA
1411 GAG
1412 AGT
1413 GTC
1414 TCC
1415 CCT
1416 CTT
1417 TTT
1418 AAT
1419 ATA
1420 TAT
1421 ATA
1422 TAA
1423 GTA
1424 TTC
1425 TCT
1426 CCA
1427 CAT
1428 ATT
1429 TTT
1430 TTT
1431 GAA
1432 AAA
1433 AAA
1434 GTC
1435 TCA
1436 CAA
1437 AAT
1438 ATA
1439 TAT
1440 ATA
1441 TAT
1442 ATC
1443 TCT
1444 CTT
1445 TTC
1446 TCT
1447 CTA
1448 TAT
1449 ATT
1450 TTG
1451 TGT
1452 GTA
1453 TAG
1454 AGA
1455 GAT
1456 ATA
1457 TAG
1458 AGA
1459 GAC
1460 ACG
1461 CGT
1462 GTC
1463 TCA
1464 CAG
1465 AGT
1466 GTC
1467 TCA
1468 CAA
1469 AAC
1470 ACT
1471 CTA
1472 TAA
1473 TGA
1474 GAT
1

2646 CCT
2647 GCC
2648 CCT
2649 CTC
2650 TCT
2651 CTA
2652 CAG
2653 ACT
2654 CTG
2655 TGT
2656 GTC
2657 TCA
2658 CAG
2659 AGA
2660 GAC
2661 ACA
2662 CAC
2663 CCT
2664 CTG
2665 TGA
2666 GAA
2667 AAA
2668 AAT
2669 ATC
2670 TCC
2671 CCC
2672 CCA
2673 CAT
2674 ATT
2675 TTC
2676 TCA
2677 CAC
2678 ACA
2679 CAG
2680 CTC
2681 TCG
2682 CGC
2683 GCA
2684 CAT
2685 ATG
2686 CAC
2687 ACT
2688 CTA
2689 TAT
2690 ATG
2691 TGT
2692 GTG
2693 TGA
2694 GAA
2695 AAA
2696 AAA
2697 AAG
2698 CTG
2699 TGT
2700 GTG
2701 TGC
2702 GCT
2703 CTT
2704 TTC
2705 GTG
2706 TGC
2707 GCA
2708 CAG
2709 AGC
2710 GCA
2711 TCT
2712 CTT
2713 TTT
2714 TTA
2715 TAA
2716 AAT
2717 ATT
2718 TTT
2719 TTG
2720 TGT
2721 GTG
2722 TGG
2723 GGG
2724 GGC
2725 GCA
2726 CAC
2727 ACA
2728 CAG
2729 CCT
2730 CCA
2731 CAC
2732 ACA
2733 CAG
2734 AGC
2735 ACA
2736 CAG
2737 AGG
2738 GGC
2739 GCT
2740 CTC
2741 TCC
2742 CCA
2743 CAG
2744 AGG
2745 GGG
2746 GGA
2747 GAA
2748 AAT
2749 ATA
2750 TAG
2751 AGG
2752 GGA
2753 TAC
2754 ACG
2755 CGG
2756 GGT
2

4114 TAT
4115 ATG
4116 TGA
4117 GAT
4118 ATT
4119 TTA
4120 TAG
4121 AGA
4122 GAA
4123 AAT
4124 ATA
4125 TAA
4126 AAT
4127 ATA
4128 TAA
4129 GCT
4130 CTA
4131 TAC
4132 ACC
4133 CCA
4134 CAT
4135 ATC
4136 TCG
4137 CGG
4138 GGG
4139 AGT
4140 GTG
4141 TGC
4142 GCC
4143 CCT
4144 CTT
4145 TTT
4146 AAT
4147 ACA
4148 CAC
4149 ACT
4150 TCC
4151 CCA
4152 CAC
4153 ACC
4154 CCA
4155 CAT
4156 ATC
4157 TCT
4158 GAT
4159 ATC
4160 TCT
4161 ATG
4162 TGG
4163 GGA
4164 CAG
4165 AGG
4166 GGA
4167 GAA
4168 AAA
4169 AAC
4170 ACG
4171 CGG
4172 GGA
4173 GAA
4174 AAA
4175 AAG
4176 ATG
4177 TGT
4178 GTT
4179 CCT
4180 CTG
4181 TCC
4182 CCA
4183 CAA
4184 AAG
4185 AGT
4186 GTC
4187 TCC
4188 ATC
4189 TCA
4190 CAG
4191 AGC
4192 GCT
4193 CTC
4194 TCT
4195 CTG
4196 TGA
4197 GAA
4198 AAG
4199 AGC
4200 GCA
4201 CAC
4202 ACA
4203 CAC
4204 ACC
4205 CCG
4206 CGG
4207 GGC
4208 GCT
4209 ATG
4210 TGG
4211 GGC
4212 GCA
4213 CAA
4214 AAC
4215 ACT
4216 CTC
4217 TCT
4218 CTG
4219 TGT
4220 GTG
4221 TGC
4222 GCT
4223 CTC
4224 TCC
4

5659 GAG
5660 AGC
5661 GCG
5662 CGC
5663 GCC
5664 TCG
5665 CGG
5666 GGG
5667 GGC
5668 GCA
5669 CAC
5670 ACT
5671 CTT
5672 TTT
5673 TTG
5674 TGG
5675 GGA
5676 GAC
5677 ACG
5678 CGC
5679 GCG
5680 CGC
5681 CCC
5682 CTG
5683 TGA
5684 GAG
5685 CTG
5686 TGT
5687 GTG
5688 TGG
5689 GGA
5690 GAT
5691 ATG
5692 TGC
5693 GCT
5694 CTG
5695 TGC
5696 GCA
5697 CAG
5698 AGT
5699 GTC
5700 TCC
5701 CCT
5702 CTG
5703 TGA
5704 GAC
5705 ACT
5706 CTT
5707 TTG
5708 TGC
5709 GCC
5710 CCA
5711 CAC
5712 ACA
5713 CAG
5714 AGC
5715 GCT
5716 CTT
5717 TTA
5718 TAG
5719 GAA
5720 CGA
5721 GAT
5722 ATC
5723 TCC
5724 CCT
5725 CTC
5726 TCA
5727 CAA
5728 AAG
5729 AGT
5730 GTG
5731 TGC
5732 GCT
5733 CTG
5734 TGA
5735 GAC
5736 ACA
5737 CAG
5738 GTC
5739 TCA
5740 CAG
5741 AGC
5742 GCC
5743 CCT
5744 CTG
5745 TGG
5746 GGC
5747 GCT
5748 CTC
5749 TCT
5750 CTG
5751 TGC
5752 GCC
5753 CCC
5754 CCA
5755 CCT
5756 CTG
5757 TGC
5758 GCT
5759 GTT
5760 TTT
5761 TTA
5762 TAC
5763 ACC
5764 CCT
5765 CTC
5766 TCC
5767 CCA
5768 CAA
5769 AAG
5

...

228576 GCC
228577 CCT
228578 CTT
228579 ACT
228580 CTG
228581 TGT
228582 GTC
228583 TCT
228584 CTT
228585 TTG
228586 TGA
228587 GAC
228588 ACA
228589 CAT
228590 ATT
228591 ATG
228592 TGA
228593 GAT
228594 ATT
228595 TTC
228596 TCA
228597 TCC
228598 CCA
228599 CAG
228600 AGG
228601 GGG
228602 GGT
228603 AGC
228604 GCC
228605 ACT
228606 CTT
228607 TTG
228608 TGC
228609 GCA
228610 CAG
228611 AGC
228612 GCT
228613 CTT
228614 TTC
228615 TCC
228616 CCC
228617 CCC
228618 CCA
228619 GCC
228620 CCT
228621 CTG
228622 TGA
228623 GAG
228624 AGC
228625 GCT
228626 CTT
228627 TTG
228628 GGC
228629 GCC
228630 CCT
228631 CTC
228632 TCC
228633 CCA
228634 CAT
228635 ATA
228636 TAG
228637 AGC
228638 GCC
228639 CCT
228640 CTC
228641 TCG
228642 CGC
228643 GCT
228644 GTC
228645 TCT
228646 CTC
228647 TCC
228648 CCT
228649 CTG
228650 TGC
228651 GCA
228652 CAC
228653 ACC
228654 ATT
228655 TTC
228656 TCC
228657 CCC
228658 CCC
228659 CCA
228660 CAA
228661 CGG
228662 GGG
228663 GGA
228664 GAG
228665 AGA
228666 GAG

229982 ATA
229983 TAT
229984 ATT
229985 TTC
229986 TCT
229987 CTT
229988 TTG
229989 TGA
229990 TCT
229991 CTG
229992 TGC
229993 GCA
229994 CAT
229995 AAA
229996 AAG
229997 AGA
229998 GAA
229999 AAT
230000 ATG
230001 TGT
230002 TAA
230003 AAA
230004 AAG
230005 AGA
230006 GAA
230007 AAA
230008 AAA
230009 AAA
230010 AAT
230011 ATG
230012 TGA
230013 GAG
230014 AGT
230015 AAA
230016 AAG
230017 AGC
230018 GCA
230019 CAT
230020 ATA
230021 TAC
230022 ACT
230023 CTC
230024 TCA
230025 CAA
230026 AAT
230027 ATA
230028 TAC
230029 ACA
230030 CAA
230031 AAT
230032 ATA
230033 TAA
230034 AAA
230035 AAA
230036 AAG
230037 AGA
230038 GAT
230039 ATT
230040 TTG
230041 TGG
230042 GGG
230043 GGC
230044 GCA
230045 CAG
230046 AGA
230047 GAA
230048 AAA
230049 AAA
230050 AAC
230051 TCA
230052 CAA
230053 AAC
230054 ACA
230055 CAA
230056 AAG
230057 AGC
230058 GCA
230059 CAT
230060 ATT
230061 TTT
230062 TTC
230063 TCA
230064 CAC
230065 ACC
230066 AGA
230067 GAG
230068 AGG
230069 GGA
230070 GAA
230071 AAA
230072 AAC

231249 AAT
231250 AGT
231251 GTG
231252 TGC
231253 GCC
231254 CCG
231255 CGG
231256 GGT
231257 GTG
231258 TGG
231259 GAA
231260 AAG
231261 AGA
231262 GAA
231263 AAG
231264 AAA
231265 AAA
231266 AAT
231267 AAA
231268 AAA
231269 AAA
231270 AAA
231271 AAG
231272 AGA
231273 GAG
231274 AGT
231275 GTG
231276 GTA
231277 TAC
231278 ACT
231279 CTT
231280 TTT
231281 TTA
231282 TAG
231283 AGA
231284 GAA
231285 AAA
231286 GCA
231287 ATG
231288 TGT
231289 GTA
231290 TAC
231291 ACA
231292 CAG
231293 AGA
231294 GAT
231295 ATA
231296 TAA
231297 AAA
231298 AAT
231299 ATC
231300 TCC
231301 CCT
231302 CTG
231303 TGA
231304 GAT
231305 CCT
231306 CTC
231307 TCC
231308 AGT
231309 GTG
231310 TGG
231311 GGC
231312 GCT
231313 CTT
231314 TTT
231315 TTC
231316 TCT
231317 CTG
231318 TGA
231319 GAT
231320 ATT
231321 TTT
231322 TTA
231323 TAT
231324 ATG
231325 TGC
231326 GCC
231327 CCA
231328 CAT
231329 ATG
231330 TGG
231331 GGA
231332 GAA
231333 AAA
231334 AAT
231335 AAA
231336 AAT
231337 ATG
231338 TTA
231339 TAA

232656 GGA
232657 GAA
232658 AAT
232659 ATT
232660 TTA
232661 TAC
232662 ACC
232663 CCT
232664 CTA
232665 CAA
232666 AAG
232667 AGA
232668 GAC
232669 ACG
232670 CGC
232671 GCT
232672 CTT
232673 TTG
232674 TGA
232675 GAT
232676 ATG
232677 TGT
232678 GTC
232679 TCC
232680 CCC
232681 CCG
232682 CGA
232683 CAT
232684 ATG
232685 GTA
232686 TAG
232687 AGC
232688 GCT
232689 CTT
232690 TTT
232691 TTA
232692 TAT
232693 ATC
232694 TCC
232695 CCT
232696 CTC
232697 TCC
232698 CCA
232699 CAA
232700 AAG
232701 AGC
232702 GCA
232703 CAA
232704 AAG
232705 AGT
232706 GTC
232707 TCA
232708 CAC
232709 ACA
232710 CAG
232711 AGG
232712 GGA
232713 GAC
232714 TGA
232715 GAT
232716 ATG
232717 TGA
232718 GAA
232719 AAA
232720 AAG
232721 AAG
232722 AGT
232723 GTC
232724 TCA
232725 CAT
232726 ATT
232727 TTC
232728 TCA
232729 CAG
232730 AGT
232731 GTG
232732 TGA
232733 GAA
232734 AAT
232735 ATG
232736 TGT
232737 GTT
232738 TTT
232739 TGG
232740 AAA
232741 AAG
232742 AGG
232743 GGC
232744 GCT
232745 CTT
232746 TTT

KeyboardInterrupt: 

In [ ]:
for i in range(len(Y)):
    print(i, decoder(Y[i]))

In [ ]:
for i in range(len(Y)):
    print(i, decoder(Y1[i]))